In [16]:
import cv2
import numpy as np
import os
# from scipy import ndimage

In [17]:
sequence_folder = 'sequence/'
frame_files = sorted([f for f in os.listdir(sequence_folder) if f.endswith('.jpg') or f.endswith('.png')])
initial_bbox = (246, 208, 23, 23) 

initial_hypothesis = np.array([initial_bbox[1], initial_bbox[0], 
                                   initial_bbox[1] + initial_bbox[3], 
                                   initial_bbox[0] + initial_bbox[2]])
frames = (cv2.imread(os.path.join(sequence_folder, f)) for f in frame_files)

In [53]:
frames = list(frames) 

In [54]:
vis_frame = frames[0]

top, left, bottom, right = initial_hypothesis
cv2.rectangle(vis_frame, (left, top), (right, bottom), (0, 255, 0), 2)
cv2.imshow('Object Tracking', vis_frame)
# cv2.waitKey(0)
key = cv2.waitKey(0) & 0xFF

In [ ]:
# hsv = cv2.cvtColor(vis_frame, cv2.COLOR_BGR2HSV)
# hist = cv2.calcHist([hsv], [2], None, [256], [0, 256])

In [13]:
hist.shape

(256, 1)

In [ ]:
cv2.destroyAllWindows()

In [71]:


def compute_histogram(image, region_mask, bins):
    """
    Compute the non-normalized histogram for a given region.
    Args:
        image: Input image (height x width x channels).
        region_mask: Binary mask of the region (height x width).
        bins: Number of bins for the histogram.

    Returns:
        Histogram of the region.
    """
    histogram = np.zeros(bins)
    print(histogram.shape)
    for c in range(image.shape[-1]):  # Loop over channels
        pixel_values = image[..., c][region_mask]  # Extract pixel values within the region
        hist, _ = np.histogram(pixel_values, bins=bins, range=(0, 256))
        histogram += hist
    return histogram

def classify_pixel(I_x, H_O, H_S):
    """
    Classify a pixel using Eq. (2) from the document.
    Args:
        I_x: The pixel's bin index.
        H_O: Histogram of the object region.
        H_S: Histogram of the surrounding region.

    Returns:
        Probability that the pixel belongs to the object.
    """
    H_O_b = H_O[I_x] if I_x < len(H_O) else 0
    H_S_b = H_S[I_x] if I_x < len(H_S) else 0
    total_hist = H_O_b + H_S_b

    if total_hist > 0:
        return H_O_b / total_hist
    else:
        # print(total_hist)
        return 0.5  # Maximum entropy prior for unseen values

def classify_image(image, object_mask, surrounding_mask, bins=256):
    """
    Classify pixels in an image using the Bayesian classifier.
    Args:
        image: Input image (height x width x channels).
        object_mask: Binary mask of the object region (height x width).
        surrounding_mask: Binary mask of the surrounding region (height x width).
        bins: Number of bins for the histogram.

    Returns:
        Probability map of object membership.
    """
    H_O = compute_histogram(image, object_mask, bins)
    H_S = compute_histogram(image, surrounding_mask, bins)
    probabilities = np.zeros(image.shape[:2])
    print(H_S.shape)
    # Normalize histograms
    # H_O = H_O / H_O.sum()
    # H_S = H_S / H_S.sum()

    for y in range(image.shape[0]):
        for x in range(image.shape[1]):
            pixel_values = image[y, x]
            bin_index = int((pixel_values.mean() / 256) * bins)  # Map pixel to bin
            
            probabilities[y, x] = classify_pixel(bin_index, H_O, H_S)
            print(probabilities[y, x], bin_index)

    return probabilities


In [21]:
# Create the object mask
object_mask = np.zeros(vis_frame.shape[:2], dtype=bool)
top, left, bottom, right = initial_hypothesis
object_mask[top:bottom, left:right] = True

In [22]:
padding = 20


# Add padding to the initial hypothesis
surrounding_top = max(0, top - padding)
surrounding_left = max(0, left - padding)
surrounding_bottom = min(vis_frame.shape[0], bottom + padding)
surrounding_right = min(vis_frame.shape[1], right + padding)

# Create the surrounding mask
surrounding_mask = np.zeros(vis_frame.shape[:2], dtype=bool)
surrounding_mask[surrounding_top:surrounding_bottom, surrounding_left:surrounding_right] = True
surrounding_mask[top:bottom, left:right] = False  # Exclude the object region

In [20]:
initial_hypothesis.shape

(4,)

In [72]:
a=classify_image(vis_frame, object_mask, surrounding_mask, )

(256,)
(256,)
(256,)
0.12121212121212122 35
0.16666666666666666 33
0.1388888888888889 31
0.25806451612903225 34
0.13333333333333333 44
0.06976744186046512 61
0.15555555555555556 78
0.2553191489361702 89
0.24489795918367346 99
0.0963855421686747 115
0.056338028169014086 135
0.078125 158
1.0 184
0.8571428571428571 191
0.07692307692307693 157
0.0963855421686747 115
0.17391304347826086 63
0.06976744186046512 61
0.09375 73
0.24489795918367346 99
0.1864406779661017 101
0.17647058823529413 87
0.19148936170212766 86
0.14893617021276595 80
0.0547945205479452 108
0.09090909090909091 148
0.11764705882352941 166
0.03636363636363636 154
0.08256880733944955 151
0.078125 158
0.08536585365853659 156
0.08256880733944955 151
0.07692307692307693 157
0.35 165
0.08843537414965986 127
0.16666666666666666 50
0.0 8
0.14285714285714285 18
0.11904761904761904 27
0.0 16
0.09230769230769231 64
0.05442176870748299 125
0.08256880733944955 151
0.07894736842105263 143
0.1864406779661017 101
0.052083333333333336 155
0

In [31]:
a.shape


(360, 640)

In [32]:
vis_frame.shape

(360, 640, 3)

In [68]:
color_map = cv2.applyColorMap((a * 255).astype(np.uint8), cv2.COLORMAP_JET)
vis_likelihood = cv2.addWeighted(vis_frame, 0.01, color_map, 0.9, 0)

In [75]:

object_mask_display = (surrounding_mask * 255).astype(np.uint8)
cv2.imshow('Object Tracking', object_mask_display)
key = cv2.waitKey(0) & 0xFF
cv2.destroyAllWindows()